## 1. Load Data From Folders
### 1.1 Environment Setup

In [1]:
import json
import os
import numpy as np
import PIL
import string
import copy
import nltk
nltk.download('stopwords')
from nltk.tokenize import sent_tokenize, word_tokenize, RegexpTokenizer
from nltk.stem.snowball import SnowballStemmer
from nltk.corpus import stopwords
os.system('conda install gensim')
import gensim
import os
import matplotlib.pyplot as plt

from sklearn.manifold import TSNE
import joblib
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import NMF, LatentDirichletAllocation

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/chuanpuluo/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


### 1.2 Load Food Images and Recipes

In [68]:
# Define Data Path ##########
recipe_root_dir = './data/'
img_root_dir = './data/img/'
#############################


arr = os.listdir(recipe_root_dir)
data = None

# Read All Recipes into data
for d in arr: 
    if '.json' in d:
        with open( recipe_root_dir + d, 'r' ) as f:
            data_temp = json.load(f)
            if data == None:
                data = data_temp
            else:
                data.update(data_temp)

print('recipe length:', len(data))
print('One Recipe Sample')
print('Key:', list(data.keys())[0] )
print('Value:', data[ list(data.keys())[0] ])

recipe length: 41243
One Recipe Sample
Key: https://www.allrecipes.com/recipe/13738/delicious-turkey-glaze/
Value: {'title': 'Delicious Turkey Glaze', 'ingredients': ['1/4 cup sugar-free organic apple juice', '1/3 cup melted butter', '1/3 cup honey'], 'instructions': 'In a small bowl, whisk together the apple cider, butter and honey.\nBrush over entire bird 45 minutes before it completes cooking. Repeat several times before removing turkey from oven.\n', 'picture_link': 'https://images.media-allrecipes.com/userphotos/250x250/24567.jpg'}


## 2. Preprocessing Data
### 2.1 Eliminate Duplicate Recipes

In [73]:
# Eliminate Duplicate Samples
seen = set()
uniq = []
duplicates = []
for sample in data:
    if sample not in seen:
        uniq.append(sample)
        seen.add(sample)
    else: duplicates.append(sample)

duplicates.sort()

print('Number of Unique Recipe:',len(uniq)) # Print the Number of Unique Recipe
print('Number of Duplicate',len(duplicates)) # Print the Number of Duplicate Recipe

# Get All Keys
original_keys = []
for k in data.keys():
    original_keys.append(k)

count = 0
for d in original_keys: 
    img_dir = copy.deepcopy(d) 
    img_dir = img_dir.replace(":","") 
    img_dir = img_dir.replace('/','') 
    img_dir = img_dir.replace('.','') 
    if os.path.exists(img_root_dir+img_dir+".jpg"):
        data[d]['image_dir'] = str(img_root_dir+img_dir+".jpg")
    else: 
        del data[d]
print('Remove Duplicate Finished!')

Number of Unique Recipe: 41242
Number of Duplicate 0
Remove Duplicate Finished!


### 2.2 Filter out common words

In [76]:
# Get All Keys
original_keys = []
for k in data.keys():
    original_keys.append(k)

stop_words = set(stopwords.words('english')) 
words_filter = ['https','www','allrecipes','com','recipe', 'iii', 'big', 'mom', 'grandma', 'fashion', 
                'best', 'good', 'old', 'world', 'award', 'winning', 'easy', 'slow','healthy','ever', 'joy','general',
               'dinner', 'simple', 'super', 'free', 'john', 'homemade', 'fresh', 'quick', 'breakfast', 'delicious']
stemmer = SnowballStemmer('english')
tokenizer = RegexpTokenizer(r'\w+')

for title_sample in original_keys:
    title_lower = title_sample.lower()
    title_token = tokenizer.tokenize( title_lower )
    title_cleaned = [ stemmer.stem(word) for word in title_token    # take away morphological affixes
                    if word not in stop_words and     # Not stop words
                    word not in words_filter and
                    stemmer.stem(word) not in words_filter and # Not strange words
                    word.isdigit() is not True and    # Not digit
                    len(word) > 2 ]                  # Have to be words
    
    # If not cleaned word left, then delete the recipe sample
    if len(title_cleaned) == 0:
        del data[title_sample]
        continue
    
    data[title_sample]['title_cleaned'] = title_cleaned

    
# Output 20 cleaned title sample
print('20 Cleaned Recipe Title example: \n >>>')
count = 20
for recipe_sample in data:
    print(data[recipe_sample]['title_cleaned'])
    count = count - 1
    if count == 0:
        break

20 Cleaned Recipe Title example: 
 >>>
['turkey', 'glaze']
['babi', 'carrot', 'bar']
['cinnamon', 'roll', 'bunni']
['nacho', 'chees', 'sauc', 'jalapeno']
['edna', 'banana', 'cranberri', 'muffin']
['bailey', 'french', 'toast']
['mari', 'pat', 'tuna', 'melt']
['kristil', 'frat', 'hous', 'cooki']
['cowboy', 'pie']
['texa', 'lizzi']
['chicken', 'chili']
['holiday', 'cranberri', 'punch']
['grill', 'steelhead', 'trout']
['gluten', 'spaghetti', 'meatbal']
['toast', 'marshmallow', 'cupcak']
['chicken', 'cauliflow', 'korma']
['blueberri', 'oatmeal', 'bar']
['quinoa', 'butternut', 'squash', 'chicken', 'goat', 'chees']
['barbequ', 'roast', 'salmon']
['mock', 'hollandais', 'sauc']


## 3. Build Category by topic model

In [78]:
title_list = []             # Recipe Title List
title_cleaned_list = []     # Cleaned Recipe Title List
key_list = []               # Key List
for recipe_sample in data:
    title_list.append(data[recipe_sample]['title'])
    title_cleaned_list.append(data[recipe_sample]['title_cleaned'])
    key_list.append(recipe_sample)

### 3.1 Build TF-IDF Features

In [81]:
# tf-idf method
title_cleaned_list_joined = [' '.join(title_sample) for title_sample in title_cleaned_list]
print('Number of recipe title:', len(title_cleaned_list_joined))
# print(title_cleaned_list_joined[0:10])

print("Extracting tf-idf features")
tfidf_vectorizer = TfidfVectorizer(max_df=0.99)
tfidf = tfidf_vectorizer.fit_transform(title_cleaned_list_joined)
tfidf_feature_names = tfidf_vectorizer.get_feature_names()
# feature names are those unique words 

import operator
def rank_terms(A, terms):
    sums = A.sum(axis=0)
    weights = {}
    for col, term in enumerate(terms):
        weights[term] = sums[0,col]
    return sorted(weights.items(), key=operator.itemgetter(1), reverse=True)

ranking = rank_terms(tfidf, tfidf_feature_names)
print('Top words:')
for i, pair in enumerate(ranking[0:30]):
    print( "%02d. %s (%.2f)" % (i+1, pair[0], pair[1]))

Number of recipe title: 41239
Extracting tf-idf features
Top words:
01. chicken (1199.92)
02. salad (835.55)
03. cake (714.79)
04. soup (662.06)
05. pie (637.10)
06. cooki (636.79)
07. chocol (611.69)
08. potato (596.85)
09. sauc (535.83)
10. chees (516.49)
11. bake (505.86)
12. bread (471.07)
13. cream (445.25)
14. casserol (433.31)
15. appl (407.94)
16. bean (405.55)
17. rice (376.54)
18. butter (370.82)
19. sweet (363.64)
20. pork (361.35)
21. roast (346.86)
22. dip (332.36)
23. beef (332.03)
24. pumpkin (328.07)
25. pasta (324.52)
26. cooker (323.40)
27. fri (319.54)
28. tomato (313.53)
29. stuf (311.23)
30. banana (297.96)


### 3.2 Non-negative Matrix Factorization

In [86]:
n_topics = 100
n_top_words = 20

# Fit the NMF model
nmf = NMF(n_components=n_topics, random_state=1, alpha=.1, l1_ratio=.5, verbose=2, max_iter=100).fit(tfidf);

violation: 1.0
violation: 0.13863110439572948
violation: 0.0612861050707163
violation: 0.030750931045120913
violation: 0.02150749908680523
violation: 0.013986897961354952
violation: 0.010432558060236295
violation: 0.00784601112679618
violation: 0.005819440662964214
violation: 0.004831102220686834
violation: 0.004379380226257517
violation: 0.004040455557065547
violation: 0.003855622037704665
violation: 0.0037182636370475344
violation: 0.0035952735832648092
violation: 0.0034531002316623787
violation: 0.003294648728072478
violation: 0.0031394447302916266
violation: 0.0028458977671355665
violation: 0.00261440324805626
violation: 0.0023765766438175813
violation: 0.0022015291270254624
violation: 0.0020257151965469506
violation: 0.0018797811282908982
violation: 0.0017616669999199967
violation: 0.0016397255559187517
violation: 0.0015624412390485333
violation: 0.0015001526716710556
violation: 0.0014489157057680925
violation: 0.0014065998655064865
violation: 0.001376110978005962
violation: 0.001

In [87]:
def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_[:100]): # just show first 10 topics  model.components_  H Matrix
        print("Topic #%d:" % topic_idx)
        print(" ".join([feature_names[i] for i in topic.argsort()[:-n_top_words - 1:-1]]))
    print()
    
print("Top Words of each topic:")
print_top_words(nmf, tfidf_feature_names, 5)

Top Words of each topic:
Topic #0:
chicken breast enchilada wing buffalo
Topic #1:
cooki mix soft raisin chewi
Topic #2:
soup lentil tortilla leek barley
Topic #3:
salad cucumb fruit macaroni summer
Topic #4:
pie crust shepherd rhubarb custard
Topic #5:
cake pound coffe upsid mix
Topic #6:
potato mash scallop gratin leek
Topic #7:
chees mac blue macaroni goat
Topic #8:
bean black white refri pinto
Topic #9:
bread wheat machin nut whole
Topic #10:
butter peanut fudg cup tart
Topic #11:
sauc bbq barbequ alfredo white
Topic #12:
casserol tater tot enchilada hash
Topic #13:
pork chop tenderloin pull loin
Topic #14:
chocol white frost cupcak mouss
Topic #15:
bake oven twice macaroni ziti
Topic #16:
cream sour frost whip irish
Topic #17:
rice wild spanish brown pilaf
Topic #18:
appl crisp caramel cider cinnamon
Topic #19:
beef stroganoff ground enchilada brisket
Topic #20:
stuf pepper shell breast crab
Topic #21:
dip artichok fruit crab layer
Topic #22:
pumpkin spice seed mapl cupcak
Topic #

In [88]:
# Calculate W Matrix
nmf_embedding = nmf.transform(tfidf)

violation: 1.0
violation: 0.005536867887818029
violation: 1.5827478096023392e-05
Converged at iteration 4


In [89]:
# Display topic number of some samples
for index in range(0, len(data)):
    print( np.argmax( nmf_embedding[index,:] )  )
    print( title_cleaned_list[index] )
    topic = nmf.components_[ np.argmax( nmf_embedding[index,:].round(2) )  ]
    print(" ".join([tfidf_feature_names[i] for i in topic.argsort()[:-5 - 1:-1]]))
    data[ key_list[index] ]['category'] = int(np.argmax( nmf_embedding[index,:].round(2) ))

45
['turkey', 'glaze']
turkey gravi meatloaf brine meatbal
68
['babi', 'carrot', 'bar']
carrot glaze ginger parsnip souffl
58
['cinnamon', 'roll', 'bunni']
roll cinnamon up cabbag spring
7
['nacho', 'chees', 'sauc', 'jalapeno']
chees mac blue macaroni goat
42
['edna', 'banana', 'cranberri', 'muffin']
cranberri relish walnut nut chutney
64
['bailey', 'french', 'toast']
french toast overnight blueberri silk
67
['mari', 'pat', 'tuna', 'melt']
tuna melt fish macaroni sear
1
['kristil', 'frat', 'hous', 'cooki']
cooki mix soft raisin chewi
4
['cowboy', 'pie']
pie crust shepherd rhubarb custard
0
['texa', 'lizzi']
chicken breast enchilada wing buffalo
75
['chicken', 'chili']
chili white vegetarian dog texa
42
['holiday', 'cranberri', 'punch']
cranberri relish walnut nut chutney
31
['grill', 'steelhead', 'trout']
grill lime marin herb cilantro
89
['gluten', 'spaghetti', 'meatbal']
spaghetti meatbal squash clam carbonara
64
['toast', 'marshmallow', 'cupcak']
french toast overnight blueberri sil

52
['cook', 'collard', 'green']
green chile bean tea collard
7
['chees', 'quesadilla', 'lunch']
chees mac blue macaroni goat
76
['cooker', 'stout', 'stew']
stew lamb irish lentil oyster
65
['hearti', 'italian', 'sausag', 'soup']
sausag smoke gravi gumbo cornbread
63
['pineappl', 'upsid', 'bundt', 'cake']
pineappl upsid hawaiian teriyaki scallop
70
['miso', 'honey', 'chicken']
honey mustard glaze wheat ginger
15
['bake', 'cod', 'foil']
bake oven twice macaroni ziti
62
['ingredi', 'cheesecak']
cheesecak mini raspberri caramel eggnog
50
['instant', 'pot', 'sloppi', 'joe']
pot instant one mash thigh
69
['philli', 'chees', 'steak', 'pasta']
steak marinad flank marin salisburi
19
['linda', 'beef', 'marinad']
beef stroganoff ground enchilada brisket
89
['broccoli', 'spaghetti', 'soup']
spaghetti meatbal squash clam carbonara
93
['jamaica', 'coffe']
ice tea coffe pop vanilla
0
['sovr', 'barriga']
chicken breast enchilada wing buffalo
20
['crab', 'seafood', 'stuf', 'shell']
stuf pepper shell br

cooker pressur pull venison rib
3
['sunday', 'fruit', 'salad']
salad cucumb fruit macaroni summer
18
['appl', 'bundt', 'cake']
appl crisp caramel cider cinnamon
90
['around', 'smoothi']
smoothi fruit berri blueberri mango
39
['chef', 'shrimp', 'etouffe']
shrimp scampi grit cajun linguin
67
['tuna', 'macaroni', 'salad']
tuna melt fish macaroni sear
45
['turkey']
turkey gravi meatloaf brine meatbal
48
['chicken', 'garlic', 'sundri', 'tomato', 'pasta']
pasta pesto primavera angel penn
1
['gingerbread', 'boy']
chicken breast enchilada wing buffalo
30
['cooker', 'chicken']
cooker pressur pull venison rib
27
['pasta', 'olio']
pasta pesto primavera angel penn
20
['stuf', 'pepper', 'soup']
stuf pepper shell breast crab
22
['pumpkin', 'casserol']
pumpkin spice seed mapl cupcak
21
['dip', 'star']
dip artichok fruit crab layer
19
['sherri', 'brais', 'beef', 'short', 'rib']
beef stroganoff ground enchilada brisket
32
['pasta', 'scallop', 'zucchini', 'tomato']
zucchini fritter relish quich skillet


chili white vegetarian dog texa
6
['potato', 'soup']
potato mash scallop gratin leek
43
['spici', 'basil', 'chicken']
spici asian hummus wing lime
9
['irish', 'soda', 'bread']
bread wheat machin nut whole
0
['jalapeno', 'chicken']
chicken breast enchilada wing buffalo
80
['fri', 'onion', 'ring']
onion caramel ring french vidalia
0
['pistachio', 'crust', 'chicken']
chicken breast enchilada wing buffalo
30
['cooker', 'spare', 'rib']
cooker pressur pull venison rib
14
['chocol', 'cake']
chocol white frost cupcak mouss
19
['beef', 'enchilada']
beef stroganoff ground enchilada brisket
0
['wonder', 'waffl']
chicken breast enchilada wing buffalo
1
['spring', 'lime', 'tea', 'cooki']
cooki mix soft raisin chewi
1
['polvoron', 'canel', 'cinnamon', 'cooki']
cooki mix soft raisin chewi
0
['pesto', 'chicken']
chicken breast enchilada wing buffalo
11
['littl', 'meat', 'loav']
chicken breast enchilada wing buffalo
0
['minut', 'nacho', 'suprem']
chicken breast enchilada wing buffalo
3
['arugula', 'sal

italian style meatbal restaur meatloaf
20
['bob', 'stuf', 'banana', 'pepper']
stuf pepper shell breast crab
1
['gingerbread', 'men', 'cooki']
cooki mix soft raisin chewi
66
['broccoli', 'chicken', 'fettuccini', 'alfredo']
broccoli rabe alfredo cheddar quich
91
['chicken', 'alfredo', 'fettuccini', 'noodl']
noodl cabbag thai bowl asian
22
['pumpkin', 'cake']
pumpkin spice seed mapl cupcak
14
['doubl', 'chocol', 'pie']
chocol white frost cupcak mouss
0
['chicken', 'tetrazzini', 'crowd']
chicken breast enchilada wing buffalo
51
['potato', 'bacon', 'salad']
bacon wrap cheddar jalapeno brussel
29
['indian', 'tomato', 'chicken']
tomato basil sun dri feta
5
['seven', 'cake']
cake pound coffe upsid mix
24
['buffalo', 'chicken', 'roast', 'potato', 'casserol']
casserol tater tot enchilada hash
26
['lemon', 'cupcak', 'blackberri', 'buttercream']
lemon poppi seed blueberri cupcak
81
['hot', 'cocoa', 'mix']
hot dog fudg wing mix
6
['bada', 'bing', 'bada', 'bang', 'potato']
potato mash scallop gratin

...

salad cucumb fruit macaroni summer
28
['southern', 'fri', 'cabbag']
fri stir pan deep oven
76
['angel', 'beef', 'stew']
stew lamb irish lentil oyster
86
['chocol', 'bourbon', 'pecan', 'pie']
pecan mapl bourbon caramel pralin
3
['asian', 'chicken', 'salad']
salad cucumb fruit macaroni summer
0
['moussaka']
chicken breast enchilada wing buffalo
16
['chocol', 'cream', 'pie']
cream sour frost whip irish
37
['sweet', 'spici', 'sweet', 'potato']
sweet sour meatbal tangi potato
0
['gerri', 'chicken', 'enchilada']
chicken breast enchilada wing buffalo
18
['american', 'appl', 'pie']
appl crisp caramel cider cinnamon
72
['red', 'velvet', 'cake']
pepper red bell velvet wine
5
['grandmoth', 'pound', 'cake']
cake pound coffe upsid mix
67
['tuna', 'noodl', 'casserol']
tuna melt fish macaroni sear
2
['vegetarian', 'kale', 'soup']
soup lentil tortilla leek barley
54
['rosemari', 'chicken', 'orang', 'mapl', 'glaze']
orang glaze ginger mandarin juic
0
['balsam', 'chicken']
chicken breast enchilada wing 

ice tea coffe pop vanilla
5
['angel', 'food', 'cake']
cake pound coffe upsid mix
50
['chicken', 'pot', 'pie']
pot instant one mash thigh
4
['american', 'shepherd', 'pie']
pie crust shepherd rhubarb custard
69
['bake', 'halibut', 'steak']
steak marinad flank marin salisburi
67
['sesam', 'sear', 'tuna']
tuna melt fish macaroni sear
5
['kitti', 'litter', 'cake']
cake pound coffe upsid mix
14
['chocol', 'brittl', 'surpris']
chocol white frost cupcak mouss
35
['sausag', 'potato', 'kale', 'soup']
sausag smoke gravi gumbo cornbread
92
['asparagus', 'quich']
asparagus quich frittata penn risotto
39
['zippi', 'summer', 'shrimp']
shrimp scampi grit cajun linguin
18
['moist', 'appl', 'crisp']
appl crisp caramel cider cinnamon
30
['cooker', 'posol']
cooker pressur pull venison rib
77
['salsa', 'meatloaf']
salsa mango watermelon verd tropic
80
['chewi', 'caramel']
onion caramel ring french vidalia
28
['crunchi', 'oven', 'fri', 'tilapia']
fri stir pan deep oven
15
['oven', 'bake', 'bbq', 'rib']
bake

pumpkin spice seed mapl cupcak
51
['killer', 'bacon', 'chees', 'dog']
bacon wrap cheddar jalapeno brussel
73
['muffuletta', 'sandwich']
sandwich cucumb spread cuban pull
87
['caribbean', 'rum', 'punch']
ball rum popcorn date sauerkraut
93
['cappuccino', 'ice']
ice tea coffe pop vanilla
70
['honey', 'duck']
honey mustard glaze wheat ginger
74
['swedish', 'pancak']
pancak wheat whole buttermilk buckwheat
69
['bourbon', 'street', 'new', 'york', 'strip', 'steak']
steak marinad flank marin salisburi
1
['ranger', 'cooki']
cooki mix soft raisin chewi
57
['shrimp', 'red', 'thai', 'curri']
curri thai chickpea lentil tofu
75
['spici', 'turkey', 'chili']
spici asian hummus wing lime
36
['grampa', 'dave', 'texa', 'chainsaw', 'bar', 'que', 'sauc']
bar granola candi date caramel
15
['lowfat', 'bake', 'chicken']
bake oven twice macaroni ziti
1
['gingerbread', 'man', 'cooki']
cooki mix soft raisin chewi
19
['barbecu', 'beef', 'liver']
beef stroganoff ground enchilada brisket
52
['billi', 'favorit', 's

chicken breast enchilada wing buffalo
59
['spice', 'brown', 'rice', 'corn']
corn chowder cob fritter cabbag
38
['chocol', 'strawberri', 'banana', 'milkshak']
strawberri shortcak rhubarb jam lemonad
54
['cranberri', 'orang', 'bread']
orang glaze ginger mandarin juic
74
['appl', 'cider', 'pancak']
pancak wheat whole buttermilk buckwheat
40
['artichok', 'bite']
dip artichok fruit crab layer
3
['ambrosia', 'salad']
salad cucumb fruit macaroni summer
32
['zucchini', 'bread']
zucchini fritter relish quich skillet
10
['peanut', 'butter', 'heaven']
butter peanut fudg cup tart
5
['prune', 'cake']
cake pound coffe upsid mix
94
['kate', 'light', 'fluffi', 'buttermilk', 'chocol', 'chip', 'waffl']
chip chocol kale dough mini
87
['time', 'popcorn', 'ball']
ball rum popcorn date sauerkraut
58
['egg', 'roll', 'wrapper']
roll cinnamon up cabbag spring
76
['hopi', 'corn', 'stew']
stew lamb irish lentil oyster
79
['scallop', 'cabbag', 'ham', 'chees']
ham glaze quich leftov loaf
78
['sugar', 'cooki', 'vii

spici asian hummus wing lime
47
['thai', 'italian', 'fusion', 'sweet', 'chile', 'chicken', 'pizza']
pizza crust dough pepperoni fruit
62
['heaven', 'raspberri', 'dessert']
chicken breast enchilada wing buffalo
0
['sambal', 'belacan']
chicken breast enchilada wing buffalo
98
['roast', 'okra', 'cherri', 'tomato']
cherri dessert cobbler cover crisp
37
['sweet', 'bourbon', 'bronz', 'butter']
sweet sour meatbal tangi potato
98
['chocol', 'cherri', 'kiss', 'cooki']
cherri dessert cobbler cover crisp
56
['cooker', 'overnight', 'oatmeal', 'appl', 'cranberri', 'walnut']
cranberri relish walnut nut chutney
26
['ming', 'lemon', 'chicken']
lemon poppi seed blueberri cupcak
54
['butternut', 'farro', 'salad', 'blood', 'orang', 'vinaigrett']
orang glaze ginger mandarin juic
46
['keto', 'cauliflow', 'bacon', 'chees', 'mash']
cauliflow mash carb gratin low
86
['sweet', 'potato', 'cake', 'mapl', 'bourbon', 'pecan']
pecan mapl bourbon caramel pralin
83
['decad', 'mocha', 'cheesecak', 'browni']
browni fud

## 4. Save Data
### 4.1 Save NMF parameters

In [90]:
# save data
joblib.dump(data, './cleaned_categoried_data.pkl')

# save category classes
joblib.dump((nmf, nmf_embedding, tfidf_feature_names), './categories.pkl')

['./categories.pkl']

In [96]:
# reload data
data = joblib.load('./cleaned_categoried_data.pkl')
nmf, nmf_embedding, tfidf_feature_names = joblib.load('./categories.pkl')

### 4.2 Classify images into categories

In [97]:
import os, sys

def if_not_exist_mkdir(directory):
    if os.path.exists(directory)==False:
        os.mkdir( directory )

# Path to be created
cleaned_data_root_path = './data_for_nn'

folders = ['/train/', '/valid/', '/test/' ]

if_not_exist_mkdir( cleaned_data_root_path )
for f in folders:
    if_not_exist_mkdir( cleaned_data_root_path + f )
    for i in range(0, 100):
        if_not_exist_mkdir( cleaned_data_root_path + f + str(i) )

In [98]:
title_list = []
title_cleaned_list = []
key_list = []
for recipe_sample in data:
    title_list.append(data[recipe_sample]['title'])
    title_cleaned_list.append(data[recipe_sample]['title_cleaned'])
    key_list.append(recipe_sample)

In [99]:
random_choice = np.random.choice( len(data), int(0.2*len(data)), replace=False)
valid_random_index = random_choice[0:int(0.5*len(random_choice))]
test_random_index = random_choice[int(0.5*len(random_choice))+1:len(random_choice)]
joblib.dump((valid_random_index, test_random_index), './index_valid_and_test.pkl')

['./index_valid_and_test.pkl']

In [100]:
import shutil

# Path to be created
train_root_path = "./data_for_nn/train/"
valid_root_path = "./data_for_nn/valid/"
test_root_path = "./data_for_nn/test/"
root_path = None

for i in range(0, len(data)):
    if i in valid_random_index:
        # move image to valid set
        root_path = valid_root_path
    elif i in test_random_index:
        # move image to test set
        root_path = test_root_path
    else:
        # move image to train set
        root_path = train_root_path

    category = data[key_list[i]]['category']
    img_dir = data[key_list[i]]['image_dir']
    img_name = img_dir[11:]
    
    #jpgfile = PIL.Image.open( img_dir ) 
    destination_dir = root_path + str(category) + "/"
    shutil.copyfile(img_dir, destination_dir+img_name )
    
    if i % 5000 == 0:
        print(str(i)+' th image categorized finished')

0 th image categorized finished
5000 th image categorized finished
10000 th image categorized finished
15000 th image categorized finished
20000 th image categorized finished
25000 th image categorized finished
30000 th image categorized finished
35000 th image categorized finished
40000 th image categorized finished
